In [42]:
import tensorflow as tf
from konlpy.tag import Okt
from tensorflow.keras import models
from tensorflow.keras import layers
from tensorflow.keras import optimizers
from tensorflow.keras import losses
from tensorflow.keras import metrics
import nltk
import re
import json
import os
import numpy as np
from tensorflow.keras.layers import Embedding, Dense, LSTM
from keras.layers import TimeDistributed

Using TensorFlow backend.


In [2]:
def read_data(filename):
    with open(filename, 'r', encoding="utf-8") as f:
        file = f.read()
        # txt 파일의 헤더(id document label)는 제외하기
        file = file.replace('\n', ' ')
        file = re.sub('[-=+,#/\?:^$.@*\"※~&%ㆍ!』\\‘|\(\)\[\]\<\>▲�`\'…》]', '', file)
        data = file.split("다음 기사에요")
        data = data[1:]
    return data

In [3]:
def tokenize(doc):
    # norm은 정규화, stem은 근어로 표시하기를 나타냄
    okt = Okt()
    return ['/'.join(t) for t in okt.pos(doc, norm=True, stem=True)]

In [4]:
if __name__ == '__main__':
    train_data = read_data('../datas/NEWS.txt')
    test_data = read_data('../datas/NEWS_SUM.txt')

In [5]:
def reviewTokenize(datas):
    for index, data in enumerate(datas):
        hangul = re.compile('[^ ㄱ-ㅣ가-힣]+') # 한글과 띄어쓰기를 제외한 모든 글자
        datas[index] = hangul.sub("", data)
    return datas

In [6]:
train_data = reviewTokenize(train_data)
test_data = reviewTokenize(test_data)

In [7]:
print(train_data)

[' 최근 아르바이트 구인 사이트에서 허위 광고로 불법 인력을 구하는 일이 반복되고 있어 대책 마련이 시급하다 지난달 일 인천에 사는 대학생 씨는 방학을 맞아 아르바이트 자리를 찾기 위해 한 구직 사이트에 접속했다  씨의 눈길을 사로잡은 것은 남구 주안동 바텐더 모집이라는 내용의 글이었다 바텐더라는 직업에 매력을 느낀 씨는 이날 오후 해당 업체를 찾아갔지만 일반 바가 아닌 호스트바였다 자신을 실장이라고 소개한 남성은 씨에게 바텐더 모집은 끝났다  도우미로 일해볼 생각은 없냐고 물었다  강압에 못 이긴 씨는 결국 하루를 일하고 나서야 사업장을 벗어날 수 있었다 씨는 생각지도 못한 경험에 상처만 받았다며 구인광고에 호스트바가 아니다라고까지 써 있었는데 명백한 허위 광고 아니냐고 말했다 최근 아르바이트 구인 사이트가 불법 인력을 구하는 목적으로 사용되는 경우가 적지 않다  경찰에 따르면 아르바이트 사이트가 보이스피싱 현금 인출책을 구하는 목적으로도 종종 이용된다 지난 월 인천삼산경찰서는 검사를 사칭한 보이스피싱 일당의 인출책 군을 붙잡았는데 군 역시 아르바이트 사이트에서 고수익 아르바이트를 구한다는 글을 보고 범행에 가담했다고 진술했다 현재 대부분의 아르바이트 사이트는 유흥업소나 불건전 업무 등에 해당하는 구인 공고 등록을 금지하고 있다  금지 항목을 피해 등록을 하더라도 모니터링을 통해 불법 사항을 걸러낼 수 있다는 게 업계 관계자의 설명이다 하지만 씨의 경우처럼 허위로 글을 올리는 것은 사전에 걸러낼 수 없는 현실이다  한 유명 아르바이트 사이트 관계자는 공고만 보고 구인 의도를 정확히 파악하기에는 어려운 점이 있다며 피해자들이 해당 업체를 신고하면 이곳을 취업 사기 업체로 등록해 다른 사람들의 피해를 방지하고 있다고 말했다 공승배기자  ', ' 공공뉴스김수연 기자  최근 친구들과 함께 재미로 모바일 채팅 어플을 설치한 씨는 자신과 동갑인 여성과 채팅을 시작했다  씨는 활발하고 호탕한 성격의 여성이 마음에 들어 적극적으로 호감을 표현했고 실제로 만나자고 여성에게

In [8]:
train_docs = [(tokenize(data), tokenize(test_data[index])) for index, data in enumerate(train_data)]

In [9]:
for doc in train_docs:
    print(doc)

(['최근/Noun', '아르바이트/Noun', '구인/Noun', '사이트/Noun', '에서/Josa', '허위/Noun', '광고/Noun', '로/Josa', '불법/Noun', '인력/Noun', '을/Josa', '구/Noun', '하다/Verb', '일이/Modifier', '반복/Noun', '되다/Verb', '있다/Adjective', '대책/Noun', '마련/Noun', '이/Josa', '시급하다/Adjective', '지난달/Noun', '일/Noun', '인천/Noun', '에/Josa', '살다/Verb', '대학생/Noun', '씨/Noun', '는/Josa', '방학/Noun', '을/Josa', '맞다/Verb', '아르바이트/Noun', '자리/Noun', '를/Josa', '찾기/Noun', '위해/Noun', '하다/Verb', '구직/Noun', '사이트/Noun', '에/Josa', '접속/Noun', '하다/Verb', '씨/Noun', '의/Josa', '눈길/Noun', '을/Josa', '사로자다/Verb', '것/Noun', '은/Josa', '남구/Noun', '주안동/Noun', '바텐더/Noun', '모집/Noun', '이라는/Josa', '내용/Noun', '의/Josa', '글/Noun', '이다/Verb', '바텐더/Noun', '라는/Josa', '직업/Noun', '에/Josa', '매력/Noun', '을/Josa', '느끼다/Verb', '씨/Noun', '는/Josa', '이/Determiner', '날/Noun', '오후/Noun', '해당/Noun', '업체/Noun', '를/Josa', '찾아가다/Verb', '일반/Noun', '바/Noun', '가/Josa', '아니다/Adjective', '호스트/Noun', '바/Noun', '이다/Verb', '자신/Noun', '을/Josa', '실장/Noun', '이라고/Josa', '소개/Noun', '한/Josa', '남성은/Noun',

In [10]:
def make_json_file(train_docs):
        if os.path.isfile('train_docs.json'):
            with open('../datas/train_docs.json', encoding="utf-8") as f:
                train_docs = json.load(f)
        else:
            train_docs = [(tokenize(data), tokenize(test_data[index])) for index, data in enumerate(train_data)]
            # JSON 파일로 저장
            with open('../datas/train_docs.json', 'w', encoding="utf-8") as make_file:
                json.dump(train_docs, make_file, ensure_ascii=False, indent="\t")
        return train_docs

In [11]:
train_docs = make_json_file(train_docs)

In [23]:
def make_selected_words(train_docs):
    tokens = [t for d in train_docs for t in d[0]]
    text = nltk.Text(tokens, name='NMSC')
    selected_words = [f[0] for f in text.vocab().most_common(10000)]
    return selected_words

In [24]:
selected_words = make_selected_words(train_docs)

In [25]:
def change_frequency(docs):
    train_x = [term_frequency(d) for d, _ in docs]
    train_y = [term_frequency(c) for _, c in docs]
    return train_x, train_y

In [26]:
def term_frequency(doc):
    return [doc.count(word) for word in selected_words]

In [27]:
train_x, train_y = change_frequency(train_docs)

In [28]:
for x in train_y:
    print(x)

[10, 17, 6, 6, 1, 3, 1, 4, 3, 6, 2, 2, 2, 2, 6, 1, 0, 2, 0, 3, 3, 3, 1, 1, 1, 2, 0, 0, 1, 0, 0, 1, 3, 0, 4, 0, 3, 1, 4, 0, 0, 0, 0, 1, 0, 3, 0, 1, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 0, 0, 2, 0, 1, 1, 0, 1, 1, 2, 1, 1, 0, 0, 0, 0, 3, 1, 3, 0, 0, 0, 1, 0, 0, 0, 3, 3, 0, 0, 0, 0, 0, 0, 0, 0, 10, 3, 0, 0, 2, 0, 1, 0, 0, 1, 0, 0, 1, 1, 0, 1, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 1, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 1, 0, 1, 0, 0, 2, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 3, 0, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 0, 0, 0, 0, 1, 0, 0, 0, 0, 1, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 

In [45]:
def modeling(x_train, y_train):
    model = models.Sequential()
    model.add(LSTM(128)) # try using a GRU instead, for fun
    model.add(LSTM(128)) # try using a GRU instead, for fun
    model.add(Dense(23))

    model.compile(optimizer=optimizers.RMSprop(lr=0.001),
                  loss=losses.binary_crossentropy,
                  metrics=[metrics.binary_accuracy])

    model.fit(x_train, y_train, epochs=10, batch_size=512)
    return model

In [30]:
def array_to_float(data):
    x_train = np.asarray(data, dtype='float32').astype('float32')
    return x_train

In [31]:
array_to_float(train_y)

array([[10., 17.,  6., ...,  0.,  0.,  0.],
       [11., 22.,  4., ...,  0.,  0.,  0.],
       [14.,  5.,  4., ...,  0.,  0.,  0.],
       ...,
       [20., 15.,  9., ...,  0.,  0.,  0.],
       [24., 15., 12., ...,  0.,  0.,  0.],
       [ 7., 14.,  3., ...,  1.,  1.,  1.]], dtype=float32)

In [46]:
model = modeling(array_to_float(train_x), array_to_float(train_y))

ValueError: Input 0 of layer sequential_7 is incompatible with the layer: expected ndim=3, found ndim=2. Full shape received: [None, 6874]